In [1]:
import netket as nk
import functions as f
import numpy as np
from importlib import reload

ModuleNotFoundError: No module named 'functions'

In [2]:
import scripts

In [3]:
reload(scripts)

<module 'scripts' from '/home/keisuke/Documents/Research/sshfs/DimerMaster/scripts/__init__.py'>

In [4]:
t_list = np.linspace(0, 50, 201)
length = [4,4]

In [5]:
hexagon = nk.machine.graph_hex(length = [4,4])

In [6]:
h = 1
V = 1

In [7]:
corr=np.load('save/corr/corr_h=1.0V=1.0l=[4, 4]n=1.0e+06a=1000000.npy')
std=np.load('save/corr/std_h=1.0V=1.0l=[4, 4]n=1.0e+06a=1000000.npy')
corr_q = np.fft.fft2(corr, axes=(0,1))
std_q = np.fft.fft2(std, axes=(0,1))
length = [4,4]

In [17]:
hex_ = nk.machine.new_hex(np.array(length))

In [8]:
index = np.argwhere(np.ones(length))

In [9]:
l = (0,0)
[*range(10, 20)]

[10, 11, 12, 13, 14, 15, 16, 17, 18, 19]

In [10]:
import scipy 
def find_exponent(y, t_list, min_interval, max_interval):
    score = None
    best_x = None
    best_params = (0, 0)
    best_interval = None
    
    if (y == 0).any():
        return best_params, best_x, best_interval, score
    
    else:
        y = np.log(y)


    for interval in range(min_interval, max_interval):
        
        for x in range(t_list.shape[0]-interval):
            (a,b)=scipy.optimize.curve_fit(lambda t,a,b: a*t + b,  t_list[x:x+interval],  y[x:x+interval], p0=(1,-1))[0]

            score_ = (((a * t_list + b - y) ** 2 )[x:x+interval].sum() + 1/interval**2 + np.exp(a*x))/interval 
            if not score:
                score = score_
                best_x = x
                best_params = (a,b)
                best_interval = interval

            elif score_ < score:
                score = score_
                best_x = x
                best_params = (a,b)
                best_interval = interval
    return best_params, best_x, best_interval, score

In [11]:
a_array = np.zeros(length)

for l in index:
    (a_array[tuple(l)],b), x, interval, score = find_exponent(np.abs(corr_q[tuple(l)]), t_list, 10, 100)

In [12]:
a_array

array([[-0.18388137, -1.3971196 , -0.1898952 , -1.3971196 ],
       [-1.11549302, -1.0596033 , -0.30339196, -1.05027289],
       [ 0.        , -0.98904216, -0.19790747, -0.98904216],
       [-1.11549302, -1.05027289, -0.30339196, -1.0596033 ]])

In [27]:
np.vstack([hex_.a1, hex_.a2]) @ np.linalg.inv(np.vstack([hex_.a1, hex_.a2]))

array([[1., 0.],
       [0., 1.]])

In [268]:
b1 = np.linalg.inv(np.vstack([hex_.a1, hex_.a2]))[:,0]
b2 = np.linalg.inv(np.vstack([hex_.a1, hex_.a2]))[:,1]

In [299]:
pos = (index @ np.vstack([b1, b2]))
rec_lattice_vec = np.zeros((6,2))
n = 0
for i in range(-1,2):
    for j in range(-1,2):
        if i +j ==0:
            continue
        rec_lattice_vec[n] = b1 * i + b2 * j 
        n += 1
        

In [300]:
rec_lattice_vec

array([[-1.        ,  0.57735028],
       [-1.        , -0.57735028],
       [ 0.        ,  1.15470056],
       [ 0.        , -1.15470056],
       [ 1.        ,  0.57735028],
       [ 1.        , -0.57735028]])

In [301]:
bri_lattice_vec = rec_lattice_vec/2
bri_cond = bri_lattice_vec/np.sum(bri_lattice_vec ** 2,axis=1).reshape(-1,1) * (-1)

def is_in_bri(x):
    return ((np.sum(x.reshape(-1,1,2) * bri_cond.reshape(1,6,2),axis=2) + 1) >= 0).all(axis=1)

In [302]:
pos_list = []
z_list = []
z = np.abs(a_array).reshape(-1)
for n, vec in enumerate(pos):
    x_ = vec
    print(n)
    for i in [0,-1,1]:
        for j in [0,-1,1]:
            x_ = vec + i * b1 + j * b2
            if is_in_bri(x_)[0]:
                pos_list.append(x_)
                z_list.append(z[n])


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15


In [303]:
pos_ = np.vstack(pos_list)
x = pos_[:,0]
y = pos_[:,1]
z = np.array(z_list)

In [311]:
import plotly.graph_objects as go

import pandas as pd

# Read data from a csv
# z_data = pd.read_csv('https://raw.githubusercontent.com/plotly/datasets/master/api_docs/mt_bruno_elevation.csv')
for j in range(4):
    trace = go.Scatter(
            x=x,
            y=y,
            hovertext=['gap = {}'.format(ele) for ele in z],
            mode = 'markers',
        showlegend=False,
            marker=dict(color= z, 
                      colorscale='Viridis', size=14, colorbar=dict(thickness=20)))
    nx, ny = (100, 100)
    x_ = np.linspace(-1, 1, nx)
    y_ = np.linspace(-1, 1, ny)
    xv, yv = np.meshgrid(x_, y_)
    _pos = np.vstack((xv.reshape(-1),yv.reshape(-1))).T
    color = is_in_bri(_pos) + 0
    
    trace1 = go.Scatter(
            x=_pos[:,0],
            y=_pos[:,1],
#             hovertext=['gap = {}'.format(ele) for ele in z],
             hoverinfo='skip',
            mode = 'markers',
            showlegend=False,
            marker=dict(color= color, opacity=0.03,
                      colorscale='bluered', size=10))

    data = [trace1, trace]
    layout = go.Layout(
        paper_bgcolor='white',
        yaxis=dict(scaleanchor="x", scaleratio=1)
    )


    fig = go.Figure(data=data, layout= layout)
    # fig.update_layout(title='Mt Bruno Elevation',
    #                   autosize=True,
    #                   width=500, height=500,
    #                   margin=dict(l=65, r=50, b=65, t=90),
    #                   yaxis_range=[-4,2],
    #                   xaxis_range=[0,6]

    #                  )

    fig.update_scenes(xaxis_visible=False, yaxis_visible=False,zaxis_visible=False )
    fig.show()

In [282]:
b1

array([1.        , 0.57735028])

In [242]:
b2

array([ 0.        , -1.15470056])

In [55]:
import plotly.graph_objects as go

import pandas as pd


fig = go.Figure(data=[go.Surface(z=np.abs(a_array).T)])

fig.update_layout(title='Energy gap of dimer excitation(h = 1.0 V = 1.0)', 
                  xaxis_title="X Axis Title",
                  autosize=False,
                  width=500, height=500,
                  margin=dict(l=65, r=50, b=65, t=90),)

fig.show()

In [152]:
a_array 

array([[-0.18388137, -1.3971196 , -0.1898952 , -1.3971196 ],
       [-1.11549302, -1.0596033 , -0.30339196, -1.05027289],
       [ 0.        , -0.98904216, -0.19790747, -0.98904216],
       [-1.11549302, -1.05027289, -0.30339196, -1.0596033 ]])

In [153]:
index = np.argwhere(np.ones((4,4))) / 4

In [154]:
x = (index @ np.vstack([hex_.a1, hex_.a2]))[:,0]
y = (index @ np.vstack([hex_.a1, hex_.a2]))[:,1]

In [148]:
z = is_in_bri(pos) + 0

In [149]:
x = bri_lattice_vec[:,0]
y = bri_lattice_vec[:,1]

In [209]:
x = pos[:,0]
y = pos[:,1]

In [151]:
import plotly.graph_objects as go

import pandas as pd

# Read data from a csv
# z_data = pd.read_csv('https://raw.githubusercontent.com/plotly/datasets/master/api_docs/mt_bruno_elevation.csv')
for j in range(4):
    trace = go.Scatter(
            x=x,
            y=y,
            mode = 'markers',
            marker=dict(color= z, 
                      colorscale='Viridis', size=5, colorbar=dict(thickness=20)))

    data = [trace]
    layout = go.Layout(
        paper_bgcolor='white',
        yaxis=dict(scaleanchor="x", scaleratio=1)
    )


    fig = go.Figure(data=data, layout= layout)
    # fig.update_layout(title='Mt Bruno Elevation',
    #                   autosize=True,
    #                   width=500, height=500,
    #                   margin=dict(l=65, r=50, b=65, t=90),
    #                   yaxis_range=[-4,2],
    #                   xaxis_range=[0,6]

    #                  )

    fig.update_scenes(xaxis_visible=False, yaxis_visible=False,zaxis_visible=False )
    fig.show()

In [205]:
find_exponent(np.abs(corr_q[2,2]), t_list, 10, 100)

((-0.19073961016142219, -2.058466994546078), 11, 19, 0.00021678254906702665)

In [146]:
y_ = (np.log(np.abs(corr_q))[l][:-1] - np.log(np.abs(corr_q))[l][1:])/(t_list[1]- t_list[0])

<ipython-input-146-c4444eaf38e9>:1: RuntimeWarning:

divide by zero encountered in log



In [159]:
from plotly import graph_objects as go
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x = t_list[1:],
        y = moving_average(y_, 3),
#         y = np.log(np.abs(corr_q))[l],
#         error_y=dict(
#             type='data', # value of error bar given in data coordinates
#             array=np.abs(std_q[l]),
#             visible=True)
    )
    
)

# fig.add_trace(
#     go.Scatter(
#         x = t_list,
#         y = (a * t_list + b),
#     )
# )
fig.show()

In [133]:
from plotly import graph_objects as go
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x = t_list,
        y = (np.real(dimer_corr1 - sub1*sub2) + np.real(dimer_corr2 - sub1*sub2))/2,
    
    )
)
fig.show()

NameError: name 'dimer_corr1' is not defined

In [ ]:
from plotly import graph_objects as go
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x = t_list,
        y = np.real(dimer_corr1 - sub1*sub2) - np.real(dimer_corr2 - sub1*sub2)
    )
)


fig.show()

In [ ]:
len(dimer_corr)

In [ ]:
Index = (dimer_basis[:,0] > 0 )
dimer_basis2 = dimer_basis[Index]
section = np.ones(dimer_basis2.shape[0])

In [ ]:
for i, dimer_base in enumerate(dimer_basis2):
    print('{}th basis'.format(i))
    print('1 index = ',np.where(dimer_base == 1)[0]+1)
    print('-1 index = ',np.where(dimer_base == -1)[0]+1)
    print('\n')
    for x in op.get_conn(dimer_base)[0][1:]:
        print(np.where(x - dimer_base != 0)[0] + 1)
    print(op.get_conn(dimer_base)[1],'\n\n','-'*20)


In [ ]:
h = functions.new_hex()


In [ ]:
h.edges_color_from_hex

In [ ]:
importlib.reload(functions)

In [ ]:
dimer_basis = o_basis[h.is_dimer_basis(o_basis)]

In [15]:
np.unique(np.array([[1,3],[3,4]]), return_counts=True)

(array([1, 3, 4]), array([1, 2, 1]))